In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import numpy as np
import random
import time
import fiftyone as fo
import fiftyone.zoo as foz
import fiftyone.brain as fob
from tqdm.notebook import tqdm, trange
from PIL import Image
import matplotlib.pyplot as plt
import torchsummary
import torchvision.transforms as transforms
from torch.utils.data import Dataset, DataLoader
import os
from torch.nn.parallel import DistributedDataParallel as DDP
import torch.distributed as dist
# import resnet18 model from pytorch
from torchvision.models import resnet18
from torch.utils.tensorboard import SummaryWriter
import mxnet as mx
from mxnet import recordio
import torch.multiprocessing as mp
from sklearn.model_selection import train_test_split
from collections import defaultdict

In [2]:
# data_iter = mx.image.ImageIter(
#     batch_size=4,
#     data_shape=(3, 112, 96),
#     path_imgrec="./faces_webface_112x112/train.rec",
#     path_imgidx="./faces_webface_112x112/train.idx",
# )
# data_iter.reset()
# for j in range(4):
#     batch = data_iter.next()
#     data = batch.data[0]
#     # print(batch)
#     label = batch.label[0].asnumpy()
#     for i in range(4):
#         ax = plt.subplot(1, 4, i + 1)
#         plt.imshow(data[i].asnumpy().astype(np.uint8).transpose((1, 2, 0)))
#         ax.set_title("class: " + str(label[i]))
#         plt.axis("off")
#     plt.show()

# # ======= Code to show single image =======#
# path_imgrec = "./faces_webface_112x112/train.rec"
# path_imgidx = "./faces_webface_112x112/train.idx"
# imgrec = recordio.MXIndexedRecordIO(path_imgidx, path_imgrec, "r")
# # %% 1 ~ 409623
# # for i in range(409623):
# for i in range(10):
#     header, s = recordio.unpack(imgrec.read_idx(i + 1))
#     img = mx.image.imdecode(s).asnumpy()
#     plt.imshow(img)
#     plt.title("id=" + str(i) + "label=" + str(header.label))
#     plt.pause(0.1)

# see how many identities are there in the dataset
path_imgidx = "./faces_webface_112x112/train.idx"
path_imgrec="./faces_webface_112x112/train.rec"
imgrec = recordio.MXIndexedRecordIO(path_imgidx, path_imgrec, "r")
ids = []
for i in range(409623):
    header, _ = recordio.unpack(imgrec.read_idx(i + 1))
    ids.append(header.label)
print(len(set(ids)))

# show how many images are in the dataset
path_imgidx = "./faces_webface_112x112/train.idx"
path_imgrec="./faces_webface_112x112/train.rec"
imgrec = recordio.MXIndexedRecordIO(path_imgidx, path_imgrec, "r")
count = 0
for i in range(409623):
    count += 1
print(count)

8076


409623


In [3]:
DIM = (112, 96)
BS = 512

In [4]:
class CASIAWebFaceDataset(Dataset):
    def __init__(self, rec_path, idx_path, property_path, transform=None):
        self.transform = transform
        self.imgrec = recordio.MXIndexedRecordIO(idx_path, rec_path, 'r')
        
        # Read property file for dataset metadata
        with open(property_path, "r") as f:
            property_str = f.read().strip()
            self.num_classes, self.img_height, self.img_width = map(int, property_str.split(','))
        
        # Parse class boundaries from idx file
        self.class_boundaries = {}
        with open(idx_path, "r") as f:
            for line in f:
                parts = line.strip().split()
                if len(parts) == 2:
                    class_id, start_idx = int(parts[0]), int(parts[1])
                    self.class_boundaries[class_id] = start_idx
        
        self.class_ids = sorted(list(self.class_boundaries.keys()))
        
        # Calculate total number of samples
        self.total_samples = 0
        for i in range(len(self.class_ids)-1):
            class_id = self.class_ids[i]
            next_class_id = self.class_ids[i+1]
            class_size = self.class_boundaries[next_class_id] - self.class_boundaries[class_id]
            self.total_samples += class_size
        
        # Add samples from the last class
        last_class_id = self.class_ids[-1]
        # Assuming we know the total number of records from property file
        self.total_samples += 10572
    
    def __len__(self):
        return self.total_samples
    
    def __getitem__(self, idx):
        # Map global index to class ID and local index
        actual_idx = idx + 1  # MXNet indices start from 1
        
        # Read record
        header, s = recordio.unpack(self.imgrec.read_idx(actual_idx))
        img = mx.image.imdecode(s).asnumpy()
        label = int(header.label)
        
        # Convert to PIL and apply transforms
        img = Image.fromarray(img)
        if self.transform:
            img = self.transform(img)
        
        return img, label

In [5]:
def find_overlapping_identities(casia_dataset, lfw_dataset):
    """Find identities that overlap between CASIA WebFace and LFW"""
    casia_identities = set()
    lfw_identities = set()
    
    # Extract all CASIA identity names
    for idx in tqdm(range(len(casia_dataset)), desc="Scanning CASIA WebFace"):
        try:
            _, label = casia_dataset[idx]
            casia_identities.add(label)
        except Exception as e:
            print(f"Error processing CASIA index {idx}: {e}")
    
    # Extract all LFW identity names
    for sample in tqdm(lfw_dataset, desc="Scanning LFW"):
        lfw_identities.add(sample.ground_truth.label)
    
    # Find overlap
    overlapping = casia_identities.intersection(lfw_identities)
    print(f"Found {len(overlapping)} overlapping identities")
    return overlapping

class FilteredCASIADataset(Dataset):
    """Wrapper dataset that filters out overlapping identities"""
    def __init__(self, base_dataset, excluded_labels):
        self.base_dataset = base_dataset
        self.excluded_labels = set(excluded_labels)
        
        # Pre-filter valid indices
        self.valid_indices = []
        for idx in tqdm(range(len(self.base_dataset)), desc="Filtering dataset"):
            try:
                _, label = self.base_dataset[idx]
                if label not in self.excluded_labels:
                    self.valid_indices.append(idx)
            except Exception as e:
                print(f"Error filtering at index {idx}: {e}")
        
        print(f"Kept {len(self.valid_indices)} out of {len(self.base_dataset)} samples")
    
    def __len__(self):
        return len(self.valid_indices)
    
    def __getitem__(self, idx):
        return self.base_dataset[self.valid_indices[idx]]

In [6]:
class CustomNormalize:
    def __call__(self, img):
        # Convert PIL image to tensor
        img = transforms.ToTensor()(img)
        # Subtract 128 and divide by 128
        img = (img * 255.0 - 128.0) / 128.0
        return img

train_preprocess = transforms.Compose([
    transforms.Resize(DIM),
    transforms.RandomHorizontalFlip(),  # Randomly flip the image horizontally
    transforms.RandomRotation(45),  # Randomly rotate the image by up to 10 degrees
    transforms.RandomVerticalFlip(),  # Randomly flip the image vertically
    transforms.ColorJitter(brightness=0.2, contrast=0.2, saturation=0.2, hue=0.2),  # Randomly change brightness, contrast, saturation, and hue
    CustomNormalize()
])

test_preprocess = transforms.Compose([
    transforms.Resize(DIM),
    transforms.RandomHorizontalFlip(),  # Randomly flip the image horizontally
    CustomNormalize()
])

In [7]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import numpy as np
import random
import time
import fiftyone as fo
import fiftyone.zoo as foz
import fiftyone.brain as fob
from tqdm.notebook import tqdm, trange
from PIL import Image
import matplotlib.pyplot as plt
import torchsummary
import torchvision.transforms as transforms
from torch.utils.data import Dataset, DataLoader
import os
from torch.nn.parallel import DistributedDataParallel as DDP
import torch.distributed as dist
# import resnet18 model from pytorch
from torchvision.models import resnet18
from torch.utils.tensorboard import SummaryWriter
import mxnet as mx
from mxnet import recordio
import torch.multiprocessing as mp
from sklearn.model_selection import train_test_split
from collections import defaultdict

In [8]:
# data_iter = mx.image.ImageIter(
#     batch_size=4,
#     data_shape=(3, 112, 96),
#     path_imgrec="./faces_webface_112x112/train.rec",
#     path_imgidx="./faces_webface_112x112/train.idx",
# )
# data_iter.reset()
# for j in range(4):
#     batch = data_iter.next()
#     data = batch.data[0]
#     # print(batch)
#     label = batch.label[0].asnumpy()
#     for i in range(4):
#         ax = plt.subplot(1, 4, i + 1)
#         plt.imshow(data[i].asnumpy().astype(np.uint8).transpose((1, 2, 0)))
#         ax.set_title("class: " + str(label[i]))
#         plt.axis("off")
#     plt.show()

# # ======= Code to show single image =======#
# path_imgrec = "./faces_webface_112x112/train.rec"
# path_imgidx = "./faces_webface_112x112/train.idx"
# imgrec = recordio.MXIndexedRecordIO(path_imgidx, path_imgrec, "r")
# # %% 1 ~ 409623
# # for i in range(409623):
# for i in range(10):
#     header, s = recordio.unpack(imgrec.read_idx(i + 1))
#     img = mx.image.imdecode(s).asnumpy()
#     plt.imshow(img)
#     plt.title("id=" + str(i) + "label=" + str(header.label))
#     plt.pause(0.1)

# see how many identities are there in the dataset
path_imgidx = "./faces_webface_112x112/train.idx"
path_imgrec="./faces_webface_112x112/train.rec"
imgrec = recordio.MXIndexedRecordIO(path_imgidx, path_imgrec, "r")
ids = []
for i in range(409623):
    header, _ = recordio.unpack(imgrec.read_idx(i + 1))
    ids.append(header.label)
print(len(set(ids)))

# show how many images are in the dataset
path_imgidx = "./faces_webface_112x112/train.idx"
path_imgrec="./faces_webface_112x112/train.rec"
imgrec = recordio.MXIndexedRecordIO(path_imgidx, path_imgrec, "r")
count = 0
for i in range(409623):
    count += 1
print(count)

8076


409623


In [9]:
DIM = (112, 96)
BS = 512

In [10]:
class CASIAWebFaceDataset(Dataset):
    def __init__(self, rec_path, idx_path, property_path, transform=None):
        self.transform = transform
        self.imgrec = recordio.MXIndexedRecordIO(idx_path, rec_path, 'r')
        
        # Read property file for dataset metadata
        with open(property_path, "r") as f:
            property_str = f.read().strip()
            self.num_classes, self.img_height, self.img_width = map(int, property_str.split(','))
        
        # Parse class boundaries from idx file
        self.class_boundaries = {}
        with open(idx_path, "r") as f:
            for line in f:
                parts = line.strip().split()
                if len(parts) == 2:
                    class_id, start_idx = int(parts[0]), int(parts[1])
                    self.class_boundaries[class_id] = start_idx
        
        self.class_ids = sorted(list(self.class_boundaries.keys()))
        
        # Calculate total number of samples
        self.total_samples = 0
        for i in range(len(self.class_ids)-1):
            class_id = self.class_ids[i]
            next_class_id = self.class_ids[i+1]
            class_size = self.class_boundaries[next_class_id] - self.class_boundaries[class_id]
            self.total_samples += class_size
        
        # Add samples from the last class
        last_class_id = self.class_ids[-1]
        # Assuming we know the total number of records from property file
        self.total_samples += 10572
    
    def __len__(self):
        return self.total_samples
    
    def __getitem__(self, idx):
        # Map global index to class ID and local index
        actual_idx = idx + 1  # MXNet indices start from 1
        
        # Read record
        header, s = recordio.unpack(self.imgrec.read_idx(actual_idx))
        img = mx.image.imdecode(s).asnumpy()
        label = int(header.label)
        
        # Convert to PIL and apply transforms
        img = Image.fromarray(img)
        if self.transform:
            img = self.transform(img)
        
        return img, label

In [11]:
def find_overlapping_identities(casia_dataset, lfw_dataset):
    """Find identities that overlap between CASIA WebFace and LFW"""
    casia_identities = set()
    lfw_identities = set()
    
    # Extract all CASIA identity names
    for idx in tqdm(range(len(casia_dataset)), desc="Scanning CASIA WebFace"):
        try:
            _, label = casia_dataset[idx]
            casia_identities.add(label)
        except Exception as e:
            print(f"Error processing CASIA index {idx}: {e}")
    
    # Extract all LFW identity names
    for sample in tqdm(lfw_dataset, desc="Scanning LFW"):
        lfw_identities.add(sample.ground_truth.label)
    
    # Find overlap
    overlapping = casia_identities.intersection(lfw_identities)
    print(f"Found {len(overlapping)} overlapping identities")
    return overlapping

class FilteredCASIADataset(Dataset):
    """Wrapper dataset that filters out overlapping identities"""
    def __init__(self, base_dataset, excluded_labels):
        self.base_dataset = base_dataset
        self.excluded_labels = set(excluded_labels)
        
        # Pre-filter valid indices
        self.valid_indices = []
        for idx in tqdm(range(len(self.base_dataset)), desc="Filtering dataset"):
            try:
                _, label = self.base_dataset[idx]
                if label not in self.excluded_labels:
                    self.valid_indices.append(idx)
            except Exception as e:
                print(f"Error filtering at index {idx}: {e}")
        
        print(f"Kept {len(self.valid_indices)} out of {len(self.base_dataset)} samples")
    
    def __len__(self):
        return len(self.valid_indices)
    
    def __getitem__(self, idx):
        return self.base_dataset[self.valid_indices[idx]]

In [12]:
class CustomNormalize:
    def __call__(self, img):
        # Convert PIL image to tensor
        img = transforms.ToTensor()(img)
        # Subtract 128 and divide by 128
        img = (img * 255.0 - 128.0) / 128.0
        return img

train_preprocess = transforms.Compose([
    transforms.Resize(DIM),
    transforms.RandomHorizontalFlip(),  # Randomly flip the image horizontally
    transforms.RandomRotation(45),  # Randomly rotate the image by up to 10 degrees
    transforms.RandomVerticalFlip(),  # Randomly flip the image vertically
    transforms.ColorJitter(brightness=0.2, contrast=0.2, saturation=0.2, hue=0.2),  # Randomly change brightness, contrast, saturation, and hue
    CustomNormalize()
])

test_preprocess = transforms.Compose([
    transforms.Resize(DIM),
    transforms.RandomHorizontalFlip(),  # Randomly flip the image horizontally
    CustomNormalize()
])

In [13]:
class AMSoftmax(nn.Module):

    def __init__(self,
                 in_feats,
                 n_classes=10572,
                 m=0.35,
                 s=30):
        super(AMSoftmax, self).__init__()
        self.m = m
        self.s = s
        self.in_feats = in_feats
        self.W = torch.nn.Parameter(torch.randn(in_feats, n_classes), requires_grad=True)
        self.ce = nn.CrossEntropyLoss()
        nn.init.xavier_normal_(self.W, gain=1)

    def forward(self, x, lb):
        assert x.size()[0] == lb.size()[0]
        assert x.size()[1] == self.in_feats
        x_norm = torch.norm(x, p=2, dim=1, keepdim=True).clamp(min=1e-9)
        x_norm = torch.div(x, x_norm)
        w_norm = torch.norm(self.W, p=2, dim=0, keepdim=True).clamp(min=1e-9)
        w_norm = torch.div(self.W, w_norm)
        costh = torch.mm(x_norm, w_norm)
        delt_costh = torch.zeros_like(costh).scatter_(1, lb.unsqueeze(1), self.m)
        costh_m = costh - delt_costh
        costh_m_s = self.s * costh_m
        loss = self.ce(costh_m_s, lb)
        return loss

In [14]:
# class AMSoftmax(nn.Module):
#     '''
#     The am softmax as seen on https://arxiv.org/pdf/1801.05599.pdf,

#         in_features: size of the embedding, eg. 512
#         n_classes: number of classes on the classification task
#         s: s parameter of loss, standard = 30.
#         m: m parameter of loss, standard = 0.4, best between 0.35 and 0.4 according to paper.

#         *inputs: tensor shaped (batch_size X embedding_size)
#         output : tensor shaped (batch_size X n_classes) AM_softmax logits for NLL_loss.

#     '''
#     def __init__(self, in_features, n_classes, s=30, m=0.4):
#         super(AMSoftmax, self).__init__()
#         self.linear = nn.Linear(in_features, n_classes, bias=False)
#         self.s = s
#         self.m = m

#     def forward(self, *inputs):
#         x_vector = F.normalize(inputs[0], p=2, dim=-1)
#         self.linear.weight.data = F.normalize(self.linear.weight.data, p=2, dim=-1)
#         logits = self.linear(x_vector)
#         scaled_logits = (logits - self.m)*self.s
#         return  scaled_logits - self._am_logsumexp(logits)

#     def _am_logsumexp(self, logits):
#         '''
#         logsumexp designed for am_softmax, the computation is numerically stable

#         '''
#         max_x = torch.max(logits, dim=-1)[0].unsqueeze(-1)
#         term1 = (self.s*(logits - (max_x + self.m))).exp()
#         term2 = (self.s * (logits - max_x)).exp().sum(-1).unsqueeze(-1) \
#                 - (self.s * (logits - max_x)).exp()
#         return self.s*max_x + (term2 + term1).log()
    


class BasicBlock(nn.Module):
    def __init__(self, in_channels, out_channels, stride=1):
        super(BasicBlock, self).__init__()
        self.conv1 = nn.Conv2d(in_channels, out_channels, kernel_size=3, stride=stride, padding=1, bias=False)
        self.bn1 = nn.BatchNorm2d(out_channels)
        self.relu = nn.ReLU(inplace=True)
        self.conv2 = nn.Conv2d(out_channels, out_channels, kernel_size=3, stride=1, padding=1, bias=False)
        self.bn2 = nn.BatchNorm2d(out_channels)
        
        self.shortcut = nn.Sequential()
        if stride != 1 or in_channels != out_channels:
            self.shortcut = nn.Sequential(
                nn.Conv2d(in_channels, out_channels, kernel_size=1, stride=stride, bias=False),
                nn.BatchNorm2d(out_channels)
            )

    def forward(self, x):
        out = self.conv1(x)
        out = self.bn1(out)
        out = self.relu(out)
        out = self.conv2(out)
        out = self.bn2(out)
        out += self.shortcut(x)
        out = self.relu(out)
        return out

class ResNet18(nn.Module):
    def __init__(self, num_classes=10):
        super(ResNet18, self).__init__()
        self.in_channels = 64
        self.conv1 = nn.Conv2d(3, 64, kernel_size=7, stride=2, padding=3, bias=False)
        self.bn1 = nn.BatchNorm2d(64)
        self.relu = nn.ReLU(inplace=True)
        self.maxpool = nn.MaxPool2d(kernel_size=3, stride=2, padding=1)
        
        self.layer1 = self._make_layer(BasicBlock, 64, 2, stride=1)
        self.layer2 = self._make_layer(BasicBlock, 128, 2, stride=2)
        self.layer3 = self._make_layer(BasicBlock, 256, 2, stride=2)
        self.layer4 = self._make_layer(BasicBlock, 512, 2, stride=2)
        
        self.avgpool = nn.AdaptiveAvgPool2d((1, 1))
        self.fc = nn.Linear(512, num_classes)

    def _make_layer(self, block, out_channels, num_blocks, stride):
        strides = [stride] + [1] * (num_blocks - 1)
        layers = []
        for stride in strides:
            layers.append(block(self.in_channels, out_channels, stride))
            self.in_channels = out_channels
        return nn.Sequential(*layers)

    def forward(self, x):
        out = self.conv1(x)
        out = self.bn1(out)
        out = self.relu(out)
        out = self.maxpool(out)
        
        out = self.layer1(out)
        out = self.layer2(out)
        out = self.layer3(out)
        out = self.layer4(out)
        
        out = self.avgpool(out)
        out = out.view(out.size(0), -1)
        out = self.fc(out)
        return out


# How can I modify the model to output embeddings of size 128?
# 1. Create a new model that outputs embeddings
# 2. Modify the last layer of the model to output embeddings
# 3. Use a hook to extract embeddings from the model
# 4. Use a custom loss function to train the model

class EmbeddingResNet18(nn.Module):
    def __init__(self, embedding_size=128, dropout=0.5):
        super(EmbeddingResNet18, self).__init__()
        self.resnet = resnet18(weights=None)
        self.resnet.fc = nn.Sequential(
            nn.Linear(512, embedding_size),
            nn.BatchNorm1d(embedding_size),
            nn.ReLU(),
            nn.Dropout(dropout)
        )
    
    def forward(self, x):
        return self.resnet(x)


In [15]:
# model = EmbeddingResNet18()
# model = model.to("cuda")
# torchsummary.summary(model, (3, 112, 96))

# model = ResNet18(num_classes=128)
# model = model.to("cuda")
# torchsummary.summary(model, (3, 112, 96))

In [16]:
def test_classifier(model, classifier, data_loader, device, message):
    model.eval()
    classifier.eval()
    correct = 0
    total = 0

    with torch.no_grad():
        for images, labels in tqdm(data_loader, desc="Testing"):
            images, labels = images.to(device), labels.to(device)
            embeddings = model(images)  # Extract features
            logits = classifier(embeddings)  # Compute AMSoftmax logits
            predictions = torch.argmax(logits, dim=1)  # Get class with max probability
            
            correct += (predictions == labels).sum().item()
            total += labels.size(0)

    accuracy = correct / total * 100
    print(f"✅ Classification Accuracy for {message}: {accuracy:.2f}%")
    return accuracy

In [17]:
def test_classifier_cosine_similarity(model, classifier, data_loader, device, message):
    model.eval()
    classifier.eval()
    correct = 0
    total = 0

    with torch.no_grad():
        for images, labels in tqdm(data_loader, desc="Testing"):
            images, labels = images.to(device), labels.to(device)
            embeddings = model(images)  # Extract features
            embeddings = F.normalize(embeddings, p=2, dim=1)
            weights = F.normalize(classifier.W, p=2, dim=0)
            logits = torch.matmul(embeddings, weights)
            predictions = torch.argmax(logits, dim=1)

            correct += (predictions == labels).sum().item()
            total += labels.size(0)

    accuracy = correct / total * 100


    print(f"✅ Classification Accuracy for {message}: {accuracy:.2f}%")
    return accuracy

In [18]:
def train_AMSoftmax(model: nn.Module, classifier: nn.Module, data_loader: DataLoader, val_loader: DataLoader,
                    optimizer: optim.Optimizer, scheduler: optim.lr_scheduler, 
                    criterion: nn.Module, epochs: int, device: torch.device, 
                    retain_graph: bool):

    train_losses = []
    classifier.eval()
    tmstmp = time.strftime("%Y%m%d-%H%M%S")
    best_loss = np.inf
    vacc = 0

    # tmstmp = "20250313-074759"

    log_dir = f"runs/112x96_ResNet18_AMSoftmax_{tmstmp}"
    writer = SummaryWriter(log_dir=log_dir)

    print(f"Started Training at {tmstmp}")
    
    for e, epoch in enumerate(tqdm(range(epochs), desc="Epochs")):
        model.train()
        running_loss = 0.0
        for i, (images, labels) in enumerate(tqdm(data_loader, desc="Batches")):
            images, labels = images.to(device), labels.to(device)
            optimizer.zero_grad()
            embeddings = model(images)  # Extract embeddings from model
            # logits = classifier(embeddings)  # Compute AMSoftmax logits
            # loss = criterion(logits, labels)  # Compute NLL loss
            loss = classifier(embeddings, labels)

            loss.backward(retain_graph=retain_graph)
            optimizer.step()
            running_loss += loss.item()
            # print(f"Batch {i+1}/{len(data_loader)} - Loss: {loss.item():.4f}")

        scheduler.step()
        avg_loss = running_loss / len(data_loader)
        train_losses.append(avg_loss)

        # Validation
        model.eval()
        running_loss = 0.0
        for i, (images, labels) in enumerate(tqdm(val_loader, desc="Validation")):
            images, labels = images.to(device), labels.to(device)
            embeddings = model(images)
            # logits = classifier(embeddings)
            # loss = criterion(logits, labels)
            loss = classifier(embeddings, labels)
            running_loss += loss.item()
            # print(f"Batch {i+1}/{len(val_loader)} - Loss: {loss.item():.4f}")


        # Log per epoch
        writer.add_scalar('Loss/train', avg_loss, epoch)
        writer.add_scalar('Loss/val', running_loss / len(val_loader), epoch)
        # if (e+1) % 10 == 0:
        #     train_acc = test_classifier_cosine_similarity(model, classifier, data_loader, device, "Training")
        #     val_acc = test_classifier_cosine_similarity(model, classifier, val_loader, device, "Validation")
        #     writer.add_scalar('Accuracy/train', train_acc, epoch)
        #     writer.add_scalar('Accuracy/val', val_acc, epoch)
        #     if val_acc > vacc:
        #         vacc = val_acc
        #         torch.save(model.state_dict(), f"{log_dir}/112x96_ResNet18_AMSoftmax_validation_{tmstmp}.pt")
        #         print(f"Saved best model with validation accuracy {vacc}")
        print(f"Epoch {epoch+1}/{epochs} - Loss: {avg_loss:.4f}")
        # Save Best Model
        if avg_loss < best_loss:
            best_loss = avg_loss
            torch.save(model.state_dict(), f"{log_dir}/112x96_ResNet18_AMSoftmax_{tmstmp}.pt")
            print(f"Saved best model with loss: {best_loss:.4f}")

    print(f"Finished Training at {time.strftime('%Y%m%d-%H%M%S')} with best validation accuracy {vacc:.4f}")
    writer.close()

    return model, train_losses, tmstmp

In [19]:
# file_path = '/home/ichitu/py-files/label_to_indices.txt'
# if os.path.exists(file_path):
#     print(f"File exists, size: {os.path.getsize(file_path)} bytes")
    
#     # Preview file content
#     with open(file_path, 'r') as f:
#         # print size of file
#         print(f.read())
# else:
#     print("File doesn't exist")

In [20]:
def train_on_casia_webface(embedding_model, classifier, device, device_ids):
    # Set up paths
    rec_path = "/home/ichitu/py-files/faces_webface_112x112/train.rec"
    idx_path = "/home/ichitu/py-files/faces_webface_112x112/train.idx"
    property_path = "/home/ichitu/py-files/faces_webface_112x112/property"

    
    # Load datasets
    print("Loading CASIA WebFace dataset...")
    casia_dataset = CASIAWebFaceDataset(
        rec_path=rec_path,
        idx_path=idx_path,
        property_path=property_path,
        transform=train_preprocess
    )

    train_idx, test_idx = train_test_split(range(len(casia_dataset)), test_size=0.15, random_state=42)
    train_dataset = torch.utils.data.Subset(casia_dataset, train_idx)
    test_dataset = torch.utils.data.Subset(casia_dataset, test_idx)
    val_idx, test_idx = train_test_split(test_idx, test_size=0.7, random_state=42)
    val_dataset = torch.utils.data.Subset(casia_dataset, val_idx)
    test_dataset = torch.utils.data.Subset(casia_dataset, test_idx)

    print(len(train_dataset))
    print(len(val_dataset))
    print(len(test_dataset))

    

    print(len(casia_dataset))
    
    # print("Loading LFW dataset...")
    # lfw_dataset = foz.load_zoo_dataset("lfw")
    
    # Find and filter overlapping identities
    # print("Finding overlapping identities...")
    # overlapping_ids = find_overlapping_identities(casia_dataset, lfw_dataset)
    
    # print("Creating filtered dataset...")
    # filtered_dataset = FilteredCASIADataset(casia_dataset, overlapping_ids)
    # filtered_dataset = casia_dataset
    
    # Create data loader
    # train_loader = DataLoader(
    #     train_dataset, 
    #     batch_size=BS * len(device_ids),
    #     shuffle=True, 
    #     num_workers=2,
    #     pin_memory=True
    # )

    # val_loader = DataLoader(
    #     val_dataset, 
    #     batch_size=BS * len(device_ids),
    #     shuffle=True, 
    #     num_workers=2,
    #     pin_memory=True
    # )

    # test_loader = DataLoader(
    #     test_dataset, 
    #     batch_size=BS * len(device_ids),
    #     shuffle=True, 
    #     num_workers=2,
    #     pin_memory=True
    # )

    train_loader = DataLoader(
        casia_dataset,
        batch_size=BS * len(device_ids),
        num_workers=4,
        sampler=torch.utils.data.SubsetRandomSampler(train_idx),
        pin_memory=True
    )

    val_loader = DataLoader(
        CASIAWebFaceDataset(
            rec_path=rec_path,
            idx_path=idx_path,
            property_path=property_path,
            transform=test_preprocess
        ),
        batch_size=BS * len(device_ids),
        num_workers=2,
        sampler=torch.utils.data.SubsetRandomSampler(val_idx),
        pin_memory=True
    )

    test_loader = DataLoader(
        CASIAWebFaceDataset(
            rec_path=rec_path,
            idx_path=idx_path,
            property_path=property_path,
            transform=test_preprocess
        ),
        batch_size=BS * len(device_ids),
        num_workers=2,
        sampler=torch.utils.data.SubsetRandomSampler(test_idx),
        pin_memory=True
    )
    
    # Set up model
    print("Setting up model...")
    
    # Set up optimizer (include both models' parameters)
    optimizer = optim.SGD(
        embedding_model.parameters(),
        lr=0.3,
        momentum=0.9,
        weight_decay=5e-4
    )
    # optimizer = optim.Adam(
    #     embedding_model.parameters(),
    #     lr=0.01,
    #     weight_decay=5e-4
    # )
    
    # Set up scheduler
    # scheduler = optim.lr_scheduler.StepLR(optimizer, step_size=100, gamma=0.1)
    # scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=300, eta_min=1e-6)
    scheduler = optim.lr_scheduler.MultiStepLR(optimizer, 
                                               milestones=[100, 150, 200, 250, 300],
                                               gamma=0.1)
    
    # Set up loss
    criterion = nn.NLLLoss()

    device = torch.device("cuda:{}".format(device_ids[1][0]) if torch.cuda.is_available() else "cpu")
    
    # Train
    print("Starting training...")
    model, losses, timestamp = train_AMSoftmax(
        model=embedding_model,
        classifier=classifier,
        data_loader=train_loader,
        val_loader=val_loader,
        optimizer=optimizer,
        scheduler=scheduler,
        criterion=criterion,
        epochs=400,  # Adjust as needed
        device=device,
        retain_graph=False,
    )

    print("Testing model...")
    # test_acc = test_classifier(embedding_model, classifier, test_loader, device, "Test")
    test_acc = 0
    
    return model, losses, timestamp, test_acc

In [21]:
# assert 1==2
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

device_ids = [[3],[3]]
classifier = AMSoftmax(512, 10572)
# embedding_model = EmbeddingResNet18(128, 0.5).to(device)
embedding_model = ResNet18(512)

if torch.cuda.device_count() > 1:
    print(f"Avaible {torch.cuda.device_count()} GPUs and using {device_ids}")
    embedding_model = nn.DataParallel(embedding_model, device_ids=device_ids[0])
    classifier = nn.DataParallel(classifier, device_ids=device_ids[1])

# embedding_model = embedding_model.to(device)
# classifier = classifier.to(device)
# embedding_model.load_state_dict(torch.load("Models-pt/112x96_ResNet18_AMSoftmax_20250313-074759.pt"))

embedding_model, train_losses, tmstmp, test_acc = train_on_casia_webface(embedding_model, classifier, device, device_ids)


Avaible 4 GPUs and using [[3], [3]]
Loading CASIA WebFace dataset...


368434
19505
45513
433452


Setting up model...
Starting training...
Started Training at 20250323-170553


Epochs:   0%|          | 0/400 [00:00<?, ?it/s]

Batches:   0%|          | 0/360 [00:00<?, ?it/s]

...

Validation:   0%|          | 0/20 [00:00<?, ?it/s]

Epoch 399/400 - Loss: 4.8508


Batches:   0%|          | 0/360 [00:00<?, ?it/s]

Validation:   0%|          | 0/20 [00:00<?, ?it/s]

Epoch 400/400 - Loss: 4.8491
Finished Training at 20250324-115151 with best validation accuracy 0.0000
Testing model...


In [22]:
print(test_acc)

0
